<a href="https://colab.research.google.com/github/jmorand1/ABCMusicLSTM/blob/main/DemoABC_LSTM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#LSTM melodies generation: Demo

# • Necessary Libraries

In [ ]:
!apt install fluidsynth
!cp /usr/share/sounds/sf2/FluidR3_GM.sf2 ./font.sf2

Reading package lists... Done
Building dependency tree       
Reading state information... Done
fluidsynth is already the newest version (2.1.1-2).
0 upgraded, 0 newly installed, 0 to remove and 24 not upgraded.


In [ ]:
import os
import regex as re
import subprocess
import urllib
import numpy as np
import tensorflow as tf
import pandas as pd

from IPython.display import Audio

import matplotlib.pyplot as plt
import time

from IPython import display as ipythondisplay
from string import Formatter

# Import all remaining packages

import functools
from tqdm import tqdm


from music21 import converter
import IPython
from IPython.display import Audio

# • Necessary Functions

In [ ]:
def extract_song_snippet(text):
    """
    Extracts song snippets from the given text.

    Args:
        text (str): The input text containing song snippets.

    Returns:
        list: A list of song snippets extracted from the text.
    """
    pattern = '(^|\n\n)(.*?)\n\n'
    search_results = re.findall(pattern, text, overlapped=True, flags=re.DOTALL)
    songs = [song[1] for song in search_results]
    print("Found {} songs in text".format(len(songs)))
    return songs

In [ ]:
def load_training_data(filepath):
    """
    Loads training data from a file and extracts song snippets.

    Args:
        filepath (str): The path to the file containing the training data.

    Returns:
        list: A list of song snippets extracted from the training data.
    """
    with open(filepath, "r") as f:
        text = f.read()
    songs = extract_song_snippet(text)
    return songs


In [ ]:
def delunlines(lines):
  """
    Delete lines from a file based on a specific condition.

    Args:
        lines (list): The lines to be checked for deletion.

    Returns:
        None
  """
  for i in lines:
    if i == 1:
      txt = "/content/dataabc.txt"
    else:
      txt = "/content/new.txt"
    with open(txt, "r") as input:
      with open("newdata.txt", "w") as output:
          # iterate all lines from file
          for line in input:
              # if line starts with substring 'time' then don't write it in temp file
              if not line.strip("\n").startswith(i):
                  output.write(line)

  # replace file with original name
    os.replace('newdata.txt', 'new.txt')

In [ ]:
### Vectorize the songs string ###

def vectorize_string(string):
  """
    Vectorizes a string by mapping characters to their corresponding indices.

    Args:
        string (str): The input string to be vectorized.

    Returns:
        numpy.ndarray: A 1-dimensional numpy array containing the vectorized output.
  """
  vectorized_output = np.array([char2idx[char] for char in string])
  return vectorized_output


In [ ]:
### Prediction of a generated song ###

def generate_text(model, start_string, generation_length=1000):
  """
    Generates text using a trained RNN model.

    Args:
        model (tf.keras.Model): The trained RNN model.
        start_string (str): The initial string to start the text generation.
        generation_length (int): The length of the generated text (default: 1000).

    Returns:
        str: The generated text.
  """
  # Evaluation step (generating ABC text using the learned RNN model)

  input_eval = [char2idx[s] for s in start_string]
  input_eval = tf.expand_dims(input_eval, 0)

  # Empty string to store our results
  text_generated = []

  # Here batch size == 1
  model.reset_states()
  tqdm._instances.clear()

  for i in tqdm(range(generation_length)):
      
      predictions = model(input_eval)
      
      predictions = tf.squeeze(predictions, 0)
      
      
      predicted_id = tf.random.categorical(predictions, num_samples=1)[-1,0].numpy()
      
      input_eval = tf.expand_dims([predicted_id], 0)
      
      
      text_generated.append(idx2char[predicted_id]) 
    
  return (start_string + ''.join(text_generated))

In [ ]:
def dispsongs(songs,songid = 1):
  """
    Display a song in ABC notation with audio playback.

    Args:
        songs (str): The song in ABC notation.
        songid (int): The identifier of the song (default: 0).

    Returns:
        None
  """
  print("\nCANCIÓN ",songid, " EN NOTACIÓN ABC\n")
  cadena = songs[songid-1]
  print(cadena,"\n")
  cadena = cadena.replace("|", "")
  print("AUDIO\n")
  s =  converter.parse(cadena, format='abc')
  s.write('midi', fp='output.mid')
  !fluidsynth -ni font.sf2 "output.mid" -F output.wav -r 44100
  IPython.display.display(Audio('output.wav'))

# • Loading Dataset

Loading Dataset in order to get character indexes

In [ ]:
#Download Dataset from Google Drive
!gdown 11UFVJ7wJyEZpj5qshmoV5qRJmUd2TH2o

Downloading...
From: https://drive.google.com/uc?id=11UFVJ7wJyEZpj5qshmoV5qRJmUd2TH2o
To: /content/dataabc.txt
100% 1.49M/1.49M [00:00<00:00, 106MB/s]


In [ ]:
filepath = '/content/dataabc.txt'
songs = load_training_data(filepath)

Found 6957 songs in text


In [ ]:
with open("/content/dataabc.txt", "r") as input:
    with open("temp.txt", "w") as output:
        # iterate all lines from file
        for line in input:
            # if line starts with substring 'time' then don't write it in temp file
            if not line.strip("\n").startswith('X:'):
                output.write(line)

# replace file with original name
os.replace('temp.txt', 'new.txt')

In [ ]:
lines = ["T:","B:","N:","Z:","O:","H:","I:","S:","R:","C:","%"]
delunlines(lines)

In [ ]:
filepath = '/content/new.txt'
songs = load_training_data(filepath)

# Print one of the songs
example_song = songs[0]
print("\nSample song: ")
print(example_song)

Found 6957 songs in text

Sample song: 
M: 2/4
L: 1/16
K:Gm
G3-A (Bcd=e) | f4 (g2dB) | ({d}c3-B) G2-E2 | F4 (D2=E^F) |
G3-A (Bcd=e) | f4 d2-f2 | (g2a2 b2).g2 | {b}(a2g2 f2).d2 |
(d2{ed}c2) B2B2 | (A2G2 {AG}F2).D2 | (GABc) (d2{ed}c>A) | G2G2 G2z ||
G | B2c2 (dcAB) | G2G2 G3G | B2d2 (gfdc) | d2g2 (g3ga) |
(bagf) (gd)d>c | (B2AG) F-D.D2 | (GABc) d2d2 | (bgfd) cA.F2 |
G2A2 (B2{cB}AG) | A3-G F2-D2 | (GABc) (d2{ed}c>A) | G2G2 G2z2 ||


In [ ]:
# Join our list of song strings into a single string containing all songs
songs_joined = "\n\n".join(songs) 

# Find all unique characters in the joined string
vocab = sorted(set(songs_joined))
print("There are", len(vocab), "unique characters in the dataset")

There are 88 unique characters in the dataset


In [ ]:
### Define numerical representation of text ###

# Create a mapping from character to unique index. 
char2idx = {u:i for i, u in enumerate(vocab)}

# Create a mapping from indices to characters. 
idx2char = np.array(vocab)

In [ ]:
pd.DataFrame(char2idx,index=[0])

\t  \n     !  "  #  &  '  (  )  ...   u   v   w   x   y   z   {   |   }   ~
0   0   1  2  3  4  5  6  7  8  9  ...  78  79  80  81  82  83  84  85  86  87

[1 rows x 88 columns]

In [ ]:
print('{')
for char,_ in zip(char2idx, range(11)):
    print('  {:4s}: {:3d},'.format(repr(char), char2idx[char]))

{
  '\t':   0,
  '\n':   1,
  ' ' :   2,
  '!' :   3,
  '"' :   4,
  '#' :   5,
  '&' :   6,
  "'" :   7,
  '(' :   8,
  ')' :   9,
  '*' :  10,


In [ ]:
vectorized_songs = vectorize_string(songs_joined)

In [ ]:
print ('{} ---- characters mapped to int ----> {}'.format(repr(songs_joined[:10]), vectorized_songs[:10]))
# check that vectorized_songs is a numpy array
assert isinstance(vectorized_songs, np.ndarray), "returned result should be a numpy array"

'M: 2/4\nL: ' ---- characters mapped to int ----> [42 26  2 18 15 20  1 41 26  2]


In [ ]:
vectorized_songs.shape

(1950045,)

# • Loading Trained Model


In [ ]:
#Download model from Google Drive
!gdown 11ztAUO3dHkRMpnsW-ZJfnpIUi0F7pA9F

Downloading...
From: https://drive.google.com/uc?id=11ztAUO3dHkRMpnsW-ZJfnpIUi0F7pA9F
To: /content/lstm.h5
100% 21.5M/21.5M [00:00<00:00, 73.8MB/s]


In [ ]:
model = tf.keras.models.load_model("/content/lstm.h5")

#model.summary()

# • Generating songs

In [ ]:
generated_text = generate_text(model, start_string="M:C\nL:1/8\nK:Am\n", generation_length=5000) 

100%|██████████| 5000/5000 [01:32<00:00, 54.12it/s]


In [ ]:
generated_songs = extract_song_snippet(generated_text)

Found 23 songs in text


In [ ]:
dispsongs(generated_songs,1)


CANCIÓN  1  EN NOTACIÓN ABC

M:C
L:1/8
K:Am
D2 | D3 E =G2 FG | AGFD CEGE | A2 GE DGAB | cABG A2 D2 |
B2 BA G2 (GA) | B2 Bd e2 dB | AGAF G2 (FG) | AGFE DEFA  |
        BAGF GFDF |     GBAG    F2 (FG) | AFDF AFDF | AGFE D2 "tr"BA |
         GFEF GAFD | AFdA BAfg | afge fdec | dBcA BG G2 |] 

AUDIO

FluidSynth runtime version 2.1.1
Copyright (C) 2000-2020 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of E-mu Systems, Inc.

Rendering audio to file 'output.wav'..
